# LET'S GOOO

---
Ida's notebook. Nothing too fancy goes on here tbh.

## Imports

In [2]:
import re
import pandas as pd
import numpy as np

import collections
from collections import Counter
import numpy
import pickle
import seaborn
import matplotlib.pyplot as plt

# nltk imports
from  nltk.metrics import agreement
from nltk.metrics.agreement import AnnotationTask
import nltk
from nltk.tokenize import TweetTokenizer
import nltk.tokenize

from nltk.lm.preprocessing import padded_everygram_pipeline, pad_both_ends
from nltk.lm import Vocabulary, MLE
from nltk.util import bigrams

# sklearn imports
from sklearn.metrics import confusion_matrix

from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer
from sklearn.linear_model import SGDClassifier

from sklearn.metrics import classification_report # same as above?
from sklearn.naive_bayes import MultinomialNB

## Loading

Irony files

In [3]:
train_irony = pd.read_csv("../datasets/irony/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_irony_labels = pd.read_csv("../datasets/irony/train_labels.txt", sep="\t", names=["labels"])

test_irony = pd.read_csv("../datasets/irony/test_text.txt", sep="\t", names=["tweets"], quoting=3)
test_irony_labels = pd.read_csv("../datasets/irony/test_labels.txt", sep="\t", names=["labels"])

validation_irony = pd.read_csv("../datasets/irony/val_text.txt", sep="\t", names=["tweets"], quoting=3)
validation_irony_labels = pd.read_csv("../datasets/irony/val_labels.txt", sep="\t", names=["labels"])

irony_mapping = pd.read_csv("../datasets/irony/mapping.txt", sep="\t", header = None, names = ["label"])

Stance files

In [4]:
train_abortion = pd.read_csv("../datasets/stance/abortion/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_abortion_labels = pd.read_csv("../datasets/stance/abortion/train_labels.txt", sep="\t", names=["labels"])
test_abortion = pd.read_csv("../datasets/stance/abortion/test_text.txt", sep="\t", names=["tweets"], quoting=3)
test_abortion_labels = pd.read_csv("../datasets/stance/abortion/test_labels.txt", sep="\t", names=["labels"])
val_abortion = pd.read_csv("../datasets/stance/abortion/val_text.txt", sep="\t", names=["tweets"], quoting=3)
val_abortion_labels = pd.read_csv("../datasets/stance/abortion/val_labels.txt", sep="\t", names=["labels"])

train_atheism = pd.read_csv("../datasets/stance/atheism/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_atheism_labels = pd.read_csv("../datasets/stance/atheism/train_labels.txt", sep="\t", names=["labels"])
test_atheism = pd.read_csv("../datasets/stance/atheism/test_text.txt", sep="\t", names=["tweets"], quoting=3)
test_atheism_labels = pd.read_csv("../datasets/stance/atheism/test_labels.txt", sep="\t", names=["labels"])
val_atheism = pd.read_csv("../datasets/stance/atheism/val_text.txt", sep="\t", names=["tweets"], quoting=3)
val_atheism_labels = pd.read_csv("../datasets/stance/atheism/val_labels.txt", sep="\t", names=["labels"])

train_climate = pd.read_csv("../datasets/stance/climate/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_climate_labels = pd.read_csv("../datasets/stance/climate/train_labels.txt", sep="\t", names=["labels"])
test_climate = pd.read_csv("../datasets/stance/climate/test_text.txt", sep="\t", names=["tweets"], quoting=3)
test_climate_labels = pd.read_csv("../datasets/stance/climate/test_labels.txt", sep="\t", names=["labels"])
val_climate = pd.read_csv("../datasets/stance/climate/val_text.txt", sep="\t", names=["tweets"], quoting=3)
val_climate_labels = pd.read_csv("../datasets/stance/climate/val_labels.txt", sep="\t", names=["labels"])

train_feminist = pd.read_csv("../datasets/stance/feminist/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_feminist_labels = pd.read_csv("../datasets/stance/feminist/train_labels.txt", sep="\t", names=["labels"])
test_feminist = pd.read_csv("../datasets/stance/feminist/train_text.txt", sep="\t", names=["tweets"], quoting=3)
test_feminist_labels = pd.read_csv("../datasets/stance/feminist/train_labels.txt", sep="\t", names=["labels"])
val_feminist = pd.read_csv("../datasets/stance/feminist/val_text.txt", sep="\t", names=["tweets"], quoting=3)
val_feminist_labels = pd.read_csv("../datasets/stance/feminist/val_labels.txt", sep="\t", names=["labels"])

train_hillary = pd.read_csv("../datasets/stance/hillary/train_text.txt", sep="\t", names=["tweets"], quoting=3)
train_hillary_labels = pd.read_csv("../datasets/stance/hillary/train_labels.txt", sep="\t", names=["labels"])
test_hillary = pd.read_csv("../datasets/stance/hillary/train_text.txt", sep="\t", names=["tweets"], quoting=3)
test_hillary_labels = pd.read_csv("../datasets/stance/hillary/train_labels.txt", sep="\t", names=["labels"])
val_hillary = pd.read_csv("../datasets/stance/hillary/val_text.txt", sep="\t", names=["tweets"], quoting=3)
val_hillary_labels = pd.read_csv("../datasets/stance/hillary/val_labels.txt", sep="\t", names=["labels"])

stance_mapping = pd.read_csv("../datasets/stance/mapping.txt", sep="\t", header = None, names = ["label"])

## Task 1: Preprocessing
Using regular expressions, implement a tokeniser to split the input texts into meaningful
tokens. Your tokeniser should be a script that takes as input the data as distributed in the
dataset and outputs the tokenised text, one output line per input line, with spaces between
tokens.

### RegEx
Links: https://www.dataquest.io/blog/regex-cheatsheet/, https://www.debuggex.com/cheatsheet/regex/python

In [69]:
#WORD = "[\w']+""
WORD = r'\w+'
WHITESPACECHARACTER = "[\s']+"
UPPER_CASE = '[A-Z]+'

trying = r'[ABCE-OQ-Za-oq-z]|(?<!:)D|(?<!:)[Pp]'


URL = '([\w\-\.]+)://([\w\-\.]+)/(\w+).(\w+)'
AT = r"^@(\w+)"
HASHTAGGED_WORD = r"#(\w+)"
WORD_HASHTAG = "#\w+"
EMOJI = "[\U00010000-\U0010ffff]"
NOT_EMOJI = "[^\U00010000-\U0010ffff]+"
SMILEYS = r"(\:\w+\:|\<[\/\\]?3|[\(\)\\\D|\*\$][\-\^]?[\:\;\=]|[\:\;\=B8][\-\^]?[3DOPp\@\$\*\\\)\(\/\|])(?=\s|[\!\.\?]|$)"


BIG = r"(\:\w+\:|\<[\/\\]?3|[\(\)\\\D|\*\$][\-\^]?[\:\;\=]|[\:\;\=B8][\-\^]?[3DOPp\@\$\*\\\)\(\/\|])(?=\s|[\!\.\?]|$) | [\U00010000-\U0010ffff]"

In [70]:
for tweet in train_irony["tweets"]:
    print(tweet)
    emo = re.findall(SMILEYS, tweet)
    emoo = re.findall(EMOJI, tweet)
    not_emo = re.findall(NOT_EMOJI, tweet)
    something = re.findall(BIG, tweet)
    print(emo)
    print(emoo)
    print(not_emo)
    print(something)

seeing ppl walking w/ crutches makes me really excited for the next 3 weeks of my life  
[]
[]
['seeing ppl walking w/ crutches makes me really excited for the next 3 weeks of my life  ']
[]
look for the girl with the broken smile, ask her if she wants to stay while, and she will be loved. 💕🎵 
[]
['💕', '🎵']
['look for the girl with the broken smile, ask her if she wants to stay while, and she will be loved. ', ' ']
['']
Now I remember why I buy books online @user #servicewithasmile  
[]
[]
['Now I remember why I buy books online @user #servicewithasmile  ']
[]
@user @user So is he banded from wearing the clothes?  #Karma 
[]
[]
['@user @user So is he banded from wearing the clothes?  #Karma ']
[]
Just found out there are Etch A Sketch apps.  #oldschool #notoldschool 
[]
[]
['Just found out there are Etch A Sketch apps.  #oldschool #notoldschool ']
[]
Hey what do you know, one of the witnesses supporting Darren Wilson's story lied! And is racist! Mind blown!  
[]
[]
["Hey what do you kn

[]
[]
['Being able to think your self angry is such a nice gift to have...  #ItsACurse ']
[]
Sad I don't have a Christmas jumper, thanks @user for your super fast delivery 👍  
[]
['👍']
["Sad I don't have a Christmas jumper, thanks @user for your super fast delivery ", '  ']
['']
@user @user Hey maybe you can reach the scoreboards and fix their latest issues  
[]
[]
['@user @user Hey maybe you can reach the scoreboards and fix their latest issues  ']
[]
#Palestinian #Authority -- #Abbas #trades #stalemate for #confrontation in #ICC #move. via @user 
[]
[]
['#Palestinian #Authority -- #Abbas #trades #stalemate for #confrontation in #ICC #move. via @user ']
[]
@user Latest album is Free The Universe #SupersonicWithGionee #Mumbai 
[]
[]
['@user Latest album is Free The Universe #SupersonicWithGionee #Mumbai ']
[]
@user has passed @user as the world's most valuable #startup! #growth #nyc 
[]
[]
["@user has passed @user as the world's most valuable #startup! #growth #nyc "]
[]
@user You're o

Wearing my @user rangers shirt, flipping off a crowd in his hometown of boston. So much  
[]
[]
['Wearing my @user rangers shirt, flipping off a crowd in his hometown of boston. So much  ']
[]
Ed Sheeran smashing out his tunes on the Victoria's Secret catwalk. Ginger legend! 
[]
[]
["Ed Sheeran smashing out his tunes on the Victoria's Secret catwalk. Ginger legend! "]
[]
You're any moment, every second,|Every scent and every flower|As a girl. 
[]
[]
["You're any moment, every second,|Every scent and every flower|As a girl. "]
[]
It's the crackhead uncle of the HBCU family "@_KKoolPoINtz_: Every HBCU in Alabama looks at Alabama State sideways lmao!" 
['_:']
[]
['It\'s the crackhead uncle of the HBCU family "@_KKoolPoINtz_: Every HBCU in Alabama looks at Alabama State sideways lmao!" ']
['_:']
@user @user yeah I'm avoiding you by waking up at 6 AM my time so by 10 PM I'm exhausted.  #sucksimissedyou <3 
['<3']
[]
["@user @user yeah I'm avoiding you by waking up at 6 AM my time so by 10 P

What a good way to start the New Year..| 
[]
[]
['What a good way to start the New Year..| ']
[]
Oh sprints I love you  
[]
[]
['Oh sprints I love you  ']
[]
idk what I love more how cold my western civ class is or western civ.  
[]
[]
['idk what I love more how cold my western civ class is or western civ.  ']
[]
.@toppscards I couldn't find the letter in my binder, but I did find these! 
[]
[]
[".@toppscards I couldn't find the letter in my binder, but I did find these! "]
[]
#NYPD  😟😕😢😪😞 not cute #NYPDMutiny I am sure the citizens feel real safe  you showed us who you are. 
[]
['😟', '😕', '😢', '😪', '😞']
['#NYPD  ', ' not cute #NYPDMutiny I am sure the citizens feel real safe  you showed us who you are. ']
['']
yeah English stop saying Jane's word 
[]
[]
["yeah English stop saying Jane's word "]
[]
My favorite color is every color. 
[]
[]
['My favorite color is every color. ']
[]
@user @user true n that's y we r jaded EVERY YEAR 
[]
[]
["@user @user true n that's y we r jaded EVERY YEA

[]
You're still shit @user #cheater #pong 
[]
[]
["You're still shit @user #cheater #pong "]
[]
@user what's the law for parking on a residential street, on the opposite side of the road facing the wrong direction? #curiosity 
[]
[]
["@user what's the law for parking on a residential street, on the opposite side of the road facing the wrong direction? #curiosity "]
[]
Getting hit on by a TSA agent who thinks my first name is Bowie #wifemeup  
[]
[]
['Getting hit on by a TSA agent who thinks my first name is Bowie #wifemeup  ']
[]
#If we're  #careful, #literacy #will #become #a #historical #blip: It's a summer... 
['p:']
[]
["#If we're  #careful, #literacy #will #become #a #historical #blip: It's a summer... "]
['p:']
Mary is not having that shit whatsoever. #done #shesdone 💁 
[]
['💁']
['Mary is not having that shit whatsoever. #done #shesdone ', ' ']
['']
It's being 200 yrs since the west had their industrial revolution but in 21st cent Ghana, an industrial de-revolution is happening. 

[]
suddenly w-wada  
[]
[]
['suddenly w-wada  ']
[]
@user long yeah. the director's cut will be longer! 😁 you need to see Penguins of Madagascar btw 
[]
['😁']
["@user long yeah. the director's cut will be longer! ", ' you need to see Penguins of Madagascar btw ']
['']
i decided to become my own boss to have more free time.. now i have no time left whatsoever.  
[]
[]
['i decided to become my own boss to have more free time.. now i have no time left whatsoever.  ']
[]
Wow I just can't wait for all the #newyearnewme posts 😂😂😂  
[]
['😂', '😂', '😂']
["Wow I just can't wait for all the #newyearnewme posts ", '  ']
['']
@user I'm hurt but I still love you 
[]
[]
["@user I'm hurt but I still love you "]
[]
EXO COMING SOON 2015||Better pray this is better with 10 members *sighs* But either way, obssessed fans would still be obssesed ._. 
[]
[]
['EXO COMING SOON 2015||Better pray this is better with 10 members *sighs* But either way, obssessed fans would still be obssesed ._. ']
[]
.@tomorrowsta

[]
[]
['Hiring Managers are willing to wait for 30Days for a guy who can join immediately, but cannot take a guy with 30Days notice period.  ']
[]
@user @user I'm sure it's largely ignored in practice. In NY you can't do any govt work if you have convicts  
[]
[]
["@user @user I'm sure it's largely ignored in practice. In NY you can't do any govt work if you have convicts  "]
[]
On page 169 of 251 of Harry Potter and the Chamber of Secrets, by J.K. Rowling 
[]
[]
['On page 169 of 251 of Harry Potter and the Chamber of Secrets, by J.K. Rowling ']
[]
#bibotour & #champwithin founder @user on @user w/dancers Ricky & Gracey #chicago #women 
[]
[]
['#bibotour & #champwithin founder @user on @user w/dancers Ricky & Gracey #chicago #women ']
[]
today is just starting out fabulous  
[]
[]
['today is just starting out fabulous  ']
[]
Think i almost just died, or burned my face off! #hategasbbqs 
[]
[]
['Think i almost just died, or burned my face off! #hategasbbqs ']
[]
new shoes. kinda in love

['@user you wearing the pin I sent for the rest of the video yesterday made my day. #daymade #addicted ']
[]
Climate change redux: CALIFORNIANS experience drought & voted for bonds to cover.Climate changed &now we have most rain in 100 years.  
['x:']
[]
['Climate change redux: CALIFORNIANS experience drought & voted for bonds to cover.Climate changed &now we have most rain in 100 years.  ']
['x:']
 Putin praising Constitutional Court for defending against 'arbitrary action on the part of the government 
[]
[]
[" Putin praising Constitutional Court for defending against 'arbitrary action on the part of the government "]
[]
Perfect time to get really sick  😫😷 
[]
['😫', '😷']
['Perfect time to get really sick  ', ' ']
['']
Jordan fan here|| 😛 -not a hater. 
[]
['😛']
['Jordan fan here|| ', ' -not a hater. ']
['']
#All #Cute #Dude #Girlygirl #I039m #Into #Is |Please RT: 
['T:']
[]
['#All #Cute #Dude #Girlygirl #I039m #Into #Is |Please RT: ']
['T:']
Hey, @user DenialCSGO decided that they wa

['Can someone please tell me where the video is? ']
[]
Wow I'm seriously dying here 🙈🙈 
[]
['🙈', '🙈']
["Wow I'm seriously dying here ", ' ']
['']
@user @user ,. #coalition fit for purpose.#Labour can and will sort it. 
[]
[]
['@user @user ,. #coalition fit for purpose.#Labour can and will sort it. ']
[]
Gah! Desperately trying to bust this cold! 
[]
[]
['Gah! Desperately trying to bust this cold! ']
[]
Girls who dip>>>  
[]
[]
['Girls who dip>>>  ']
[]
#newjob Urgent CONTRACT - Assurance Manager - Private Banking, Singapore - Not Specified, Singapore  Specifie... 
[]
[]
['#newjob Urgent CONTRACT - Assurance Manager - Private Banking, Singapore - Not Specified, Singapore  Specifie... ']
[]
@user , former Chairwoman, US Commission on Civil Rights 
[]
[]
['@user , former Chairwoman, US Commission on Civil Rights ']
[]
TNT replaying the Cavs-Knicks game...maybe the knicks will win this time  
[]
[]
['TNT replaying the Cavs-Knicks game...maybe the knicks will win this time  ']
[]
@user @use

In [170]:
EMOJI = "[\U00010000-\U0010ffff]"
EMOJICON = r"(\:\w+\:|\<[\/\\]?3|[\(\)\\\D|\*\$][\-\^]?[\:\;\=]|[\:\;\=B8][\-\^]?[3DOPp\@\$\*\\\)\(\/\|])(?=\s|[\!\.\?]|$)"
# https://stackoverflow.com/questions/28077049/regex-matching-emoticons

def emoji_cons(tweet):
    """
    Keeps tokens that are emojies or emojicons
    """
    tokens = []
    unmatchables = []

    for string in tweet:
        if re.findall(EMOJI, string) != []:
            x = re.findall(EMOJI, string)
            for element in x:
                tokens.append(re.findall(EMOJI, string))
        elif re.findall(EMOJICON, string) != []:

            tokens.append(re.findall(EMOJICON, string))
    if re.findall(EMOJICON, tweet) != []:
        tokens.append(re.findall(EMOJICON, tweet))

    if re.findall(r'[^\U00010000-\U0010ffff]+', tweet) != [] and re.findall(r'[^\U00010000-\U0010ffff]+', tweet) not in tokens:
        unmatchables.append(re.findall(r'[^\U00010000-\U0010ffff]+', tweet))

    return (tokens, unmatchables)


[]

In [152]:
for tweet in train_irony["tweets"]:
    x = emoji_cons(tweet)
    print(x)

([], [['seeing ppl walking w/ crutches makes me really excited for the next 3 weeks of my life  ']])
([['💕'], ['🎵']], [['look for the girl with the broken smile, ask her if she wants to stay while, and she will be loved. ', ' ']])
([], [['Now I remember why I buy books online @user #servicewithasmile  ']])
([], [['@user @user So is he banded from wearing the clothes?  #Karma ']])
([], [['Just found out there are Etch A Sketch apps.  #oldschool #notoldschool ']])
([], [["Hey what do you know, one of the witnesses supporting Darren Wilson's story lied! And is racist! Mind blown!  "]])
([], [['@user on stage at #flzjingleball at the @user in #Tampa #iheartradio ']])
([], [["You know it's going to be a great day when you're Garmin resets itself and you spill some cinnamon down yourself  #slowclap "]])
([], [['Halfway thorough my workday ... Woooo  ']])
([], [['Would like to thank my nephew for giving me his horrible cold & sore throat etc.. Much appreciated!  ']])
([], [["I forked node!  G

([], [['#TeensAnalyzed  Not expirienced, but cock hungry ']])
([], [['@user Be more narrow with that knife, you might just find the target to answer that. -Sarcastic. ']])
([], [['Drudgery personified #commuterprobs #northernline #tfl ']])
([], [['@user @user @user @user @user  nice to see the ambulance service is so important to OUR mps  ']])
([], [['@user illridewithyou  ']])
([], [['dressing gown on, turkey and buffalo sauce sandwich in hand and big fat quiz of the year  #moving #ever #again ']])
([], [['#Sopping #wet|#Squishing #mud #between #toes...||Well, why ...|#Swimming in a #mud #puddle ']])
([], [["@user Thanks. I'll have to check out another store in Calgary. "]])
([['💋']], [['Next day makeup just looks so hawt ', '  ']])
([], [["@user Email me when you need a friend...always here to chat, I've been there many many times so right with you xx "]])
([], [['My grandma tells me she made raviolis to eat.. You know I yelled back "fuck you I don\'t want no ravioli nigga!!!" ']])
(

([], [['Those mini naps I had all night between sneezing, coughing and blowing my nose were super restful.  #fluday4 ']])
([], [["102° fever. That's fun.  "]])
([], [['Day 39&40  3 #Novel Train. #comfortzone #christmastree #nextlevel #buzzkillington #familyguy... via @user ']])
([], [['@user So Monday it is ,tickets on general sale for boxing day.thanks for your help ']])
([], [["@user @user you do not afford the same treatment to PO's .Goes both ways. "]])
([], [['I think Apple should make their iCloud service and options a little more confusing. Its really getting good now.  ']])
([], [['Having a night in with Misha (she still needs twitter), chinese and movies all night #unilife #nightin ']])
([], [['I\'m actually kinda surprised that people still say "NOT!" after an \'ironic\' statement.   ']])
([['😣'], ['😷']], [['Beautiful way to start my morning.  ', ' ']])
([], [['Alright who was dreaming about me last night because I could not for the life of me fall asleep ']])
([], [['Togepi 

In [7]:
for tweet in train_irony["tweets"]:
    spl = re.split("\s+", tweet)
    print("spl", spl)
    for i in spl:
        word = re.findall("\w+", i)
        print("word:", word)
        print(i)

spl ['seeing', 'ppl', 'walking', 'w/', 'crutches', 'makes', 'me', 'really', 'excited', 'for', 'the', 'next', '3', 'weeks', 'of', 'my', 'life', '']
word: ['seeing']
seeing
word: ['ppl']
ppl
word: ['walking']
walking
word: ['w']
w/
word: ['crutches']
crutches
word: ['makes']
makes
word: ['me']
me
word: ['really']
really
word: ['excited']
excited
word: ['for']
for
word: ['the']
the
word: ['next']
next
word: ['3']
3
word: ['weeks']
weeks
word: ['of']
of
word: ['my']
my
word: ['life']
life
word: []

spl ['look', 'for', 'the', 'girl', 'with', 'the', 'broken', 'smile,', 'ask', 'her', 'if', 'she', 'wants', 'to', 'stay', 'while,', 'and', 'she', 'will', 'be', 'loved.', '💕🎵', '']
word: ['look']
look
word: ['for']
for
word: ['the']
the
word: ['girl']
girl
word: ['with']
with
word: ['the']
the
word: ['broken']
broken
word: ['smile']
smile,
word: ['ask']
ask
word: ['her']
her
word: ['if']
if
word: ['she']
she
word: ['wants']
wants
word: ['to']
to
word: ['stay']
stay
word: ['while']
while,
word: ['an

word: ['helpful']
helpful
word: []

spl ['I', 'refuse', 'to', 'be', 'weak...', '#workout', '#motivation', '#fitfam', '']
word: ['I']
I
word: ['refuse']
refuse
word: ['to']
to
word: ['be']
be
word: ['weak']
weak...
word: ['workout']
#workout
word: ['motivation']
#motivation
word: ['fitfam']
#fitfam
word: []

spl ['Why', 'YES!', 'Of', 'course', 'I', 'use', 'a', 'lot', 'in', 'my', 'day....because', 'violence', 'is', 'illegal.', '']
word: ['Why']
Why
word: ['YES']
YES!
word: ['Of']
Of
word: ['course']
course
word: ['I']
I
word: ['use']
use
word: ['a']
a
word: ['lot']
lot
word: ['in']
in
word: ['my']
my
word: ['day', 'because']
day....because
word: ['violence']
violence
word: ['is']
is
word: ['illegal']
illegal.
word: []

spl ['@user', '@user', '@user', 'no', 'duh.', '?', 'Is', 'will', 'owners', 'fire', 'Goodell', 'for', 'it?', 'My', 'guess', 'he', 'gets', 'a', 'raise', '#GoodellMustGo', '']
word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: ['no']
no
word: ['duh']
duh.
wo

word: ['I']
I
word: ['get']
get
word: ['to']
to
word: ['you']
you!
word: []

spl ['', 'a', 'bad', 'game', 'last', 'night.', 'Way', 'to', 'go', 'Packers!', '']
word: []

word: ['a']
a
word: ['bad']
bad
word: ['game']
game
word: ['last']
last
word: ['night']
night.
word: ['Way']
Way
word: ['to']
to
word: ['go']
go
word: ['Packers']
Packers!
word: []

spl ['I', 'hope', 'I', 'could', 'recover', 'from', 'fever', 'today.', 'I', 'need', 'to', 'start', 'with', 'strama..', '']
word: ['I']
I
word: ['hope']
hope
word: ['I']
I
word: ['could']
could
word: ['recover']
recover
word: ['from']
from
word: ['fever']
fever
word: ['today']
today.
word: ['I']
I
word: ['need']
need
word: ['to']
to
word: ['start']
start
word: ['with']
with
word: ['strama']
strama..
word: []

spl ['somebody', 'wake', 'me', 'up', 'early', 'tomorrow', 'ive', 'been', 'facing', 'weird', 'aches', 'in', 'my', 'back', 'since', 'early', 'december', '.,.', 'and', 'why', 'do', 'u', 'think', 'that', 'relates', 'madaka', '']
word: ['someb

word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: []

spl ['@user', '@user', 'Money', '4', 'Church|http://t.co/Q2WB7riAvK|SmartPhone', 'APP', 'PAYS', 'you!|See-http://t.co/RDlRuGN0iE', '|Go', '2:', '']
word: ['user']
@user
word: ['user']
@user
word: ['Money']
Money
word: ['4']
4
word: ['Church', 'http', 't', 'co', 'Q2WB7riAvK', 'SmartPhone']
Church|http://t.co/Q2WB7riAvK|SmartPhone
word: ['APP']
APP
word: ['PAYS']
PAYS
word: ['you', 'See', 'http', 't', 'co', 'RDlRuGN0iE']
you!|See-http://t.co/RDlRuGN0iE
word: ['Go']
|Go
word: ['2']
2:
word: []

spl ['Well', "it's", 'always', 'a', 'good', 'time', 'losing', 'at', 'the', 'Bay...', '@user', '@user', '@user', '']
word: ['Well']
Well
word: ['it', 's']
it's
word: ['always']
always
word: ['a']
a
word: ['good']
good
word: ['time']
time
word: ['losing']
losing
word: ['at']
at
word: ['the']
the
word: ['Bay']
Bay...
word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: []

spl ['Welsh', 'devolution?', "How's", 'th

word: ['we', 're']
we're
word: ['back']
back
word: ['in']
in
word: ['the']
the
word: ['ER']
ER.
word: ['Hooray']
Hooray
word: ['for']
for
word: ['no']
no
word: ['sleep']
sleep!
word: []

spl ['Just', 'a', 'had', 'a', 'Bruce', 'Springsteen', 'flashback.', '*shudder*', '@user', '@user', '@user', '@user', '@user', '']
word: ['Just']
Just
word: ['a']
a
word: ['had']
had
word: ['a']
a
word: ['Bruce']
Bruce
word: ['Springsteen']
Springsteen
word: ['flashback']
flashback.
word: ['shudder']
*shudder*
word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: ['user']
@user
word: []

spl ['Is', 'Obamacare', 'Slowing', 'Health', 'Care', 'Spending?', 'via', '@user', '']
word: ['Is']
Is
word: ['Obamacare']
Obamacare
word: ['Slowing']
Slowing
word: ['Health']
Health
word: ['Care']
Care
word: ['Spending']
Spending?
word: ['via']
via
word: ['user']
@user
word: []

spl ['Sessions!!', '#why', '#scary', '#canary', '#sydney', '#australia', 'by', 'lavin56', '']
word: ['Sessi

...

word: ['About']
About
word: ['to']
to
word: ['write']
write
word: ['my']
my
word: ['math']
math
word: ['final']
final
word: ['really']
really
word: ['excited']
excited
word: ['somethingrandom']
#somethingrandom
word: []

spl ['@user', '@user', 'As', 'a', 'Red', 'Sox', 'follower,', 'I', 'can', 'vouch', 'for', 'Gomes', 'as', 'a', 'clubhouse', 'leader.', 'Such', 'a', 'fun', 'teammate.', '']
word: ['user']
@user
word: ['user']
@user
word: ['As']
As
word: ['a']
a
word: ['Red']
Red
word: ['Sox']
Sox
word: ['follower']
follower,
word: ['I']
I
word: ['can']
can
word: ['vouch']
vouch
word: ['for']
for
word: ['Gomes']
Gomes
word: ['as']
as
word: ['a']
a
word: ['clubhouse']
clubhouse
word: ['leader']
leader.
word: ['Such']
Such
word: ['a']
a
word: ['fun']
fun
word: ['teammate']
teammate.
word: []

spl ['@user', 'left', 'out', 'blue', 'bin', 'as', 'per', 'calendar', 'but', 'not', 'lifted.', 'Checked', 'your', 'website', 'and', 'it', 'indicates', 'green', 'bin', 'happy', '']
word: ['user']
@user
wo

for
word: ['more']
more
word: ['of']
of
word: ['this']
this
word: ['crap']
crap.
word: ['ThanksObama']
#ThanksObama
word: ['bad']
#bad
word: []

spl ['We', 'need', 'a', '#Democracy', '#CoPocracy!!!', '#Police,', '#MorningJoe!', '#BlackLivesMatter', '#DemocracyMatters', '#Ferguson', '#EricGarner', '']
word: ['We']
We
word: ['need']
need
word: ['a']
a
word: ['Democracy']
#Democracy
word: ['CoPocracy']
#CoPocracy!!!
word: ['Police']
#Police,
word: ['MorningJoe']
#MorningJoe!
word: ['BlackLivesMatter']
#BlackLivesMatter
word: ['DemocracyMatters']
#DemocracyMatters
word: ['Ferguson']
#Ferguson
word: ['EricGarner']
#EricGarner
word: []

spl ['Yeah,', 'the', 'prom', 'is', 'the', 'most', 'important', 'event', 'in', 'your', 'life', '']
word: ['Yeah']
Yeah,
word: ['the']
the
word: ['prom']
prom
word: ['is']
is
word: ['the']
the
word: ['most']
most
word: ['important']
important
word: ['event']
event
word: ['in']
in
word: ['your']
your
word: ['life']
life
word: []

spl ['Well', 'today', 'can', 'go

word: ['they']
they
word: ['might']
might
word: ['already']
already
word: ['know']
know
word: ['him']
him!
word: ['Ferguson']
#Ferguson
word: ['NYC']
#NYC
word: []

spl ['The', 'worst', 'is', 'when', 'they', 'consider', 'things', 'like', '"conservative', 'tribune"', 'as', 'a', 'credible', 'source', 'of', 'information.', 'Totally', 'not', 'bias.', '']
word: ['The']
The
word: ['worst']
worst
word: ['is']
is
word: ['when']
when
word: ['they']
they
word: ['consider']
consider
word: ['things']
things
word: ['like']
like
word: ['conservative']
"conservative
word: ['tribune']
tribune"
word: ['as']
as
word: ['a']
a
word: ['credible']
credible
word: ['source']
source
word: ['of']
of
word: ['information']
information.
word: ['Totally']
Totally
word: ['not']
not
word: ['bias']
bias.
word: []

spl ['Not', 'even', '8am', 'and', 'I', 'can', 'already', 'see', 'this', 'is', 'going', 'to', 'be', 'a', 'wonderful', 'day', '#needmorecoffee', '']
word: ['Not']
Not
word: ['even']
even
word: ['8am']
8am
word

a
word: ['y']
y!
word: ['valueformoneynot']
#valueformoneynot
word: []

spl ["That's", 'nice.', '']
word: ['That', 's']
That's
word: ['nice']
nice.
word: []

spl ['2', '1/2', 'hour', 'nap', 'then', 'up', 'for', 'a', 'ct', 'scan', 'at', 'the', 'hospital.', 'perfect', 'timing.', '']
word: ['2']
2
word: ['1', '2']
1/2
word: ['hour']
hour
word: ['nap']
nap
word: ['then']
then
word: ['up']
up
word: ['for']
for
word: ['a']
a
word: ['ct']
ct
word: ['scan']
scan
word: ['at']
at
word: ['the']
the
word: ['hospital']
hospital.
word: ['perfect']
perfect
word: ['timing']
timing.
word: []

spl ['I', 'can', 'be', 'mad', 'at', 'you', 'for', 'a', 'matter', 'of', '15', 'min', 'then', 'I', "can't", 'stand', 'not', 'talking', 'to', 'you.', '']
word: ['I']
I
word: ['can']
can
word: ['be']
be
word: ['mad']
mad
word: ['at']
at
word: ['you']
you
word: ['for']
for
word: ['a']
a
word: ['matter']
matter
word: ['of']
of
word: ['15']
15
word: ['min']
min
word: ['then']
then
word: ['I']
I
word: ['can', 't']
can't
w

Uhhh
word: ['can', 't']
can't
word: ['sleep']
sleep
word: ['someone']
someone
word: ['like']
like
word: ['n']
n
word: ['I', 'll']
I'll
word: ['text']
text
word: ['u']
u
word: ['my']
my
word: ['phones']
phones
word: ['dry']
dry
word: ['ass']
ass
word: ['fuck']
fuck
word: ['fr']
fr
word: ['am']
#am
word: ['a']
#a
word: ['boring', 'person']
#boring#person
word: []

spl ['Vacations...re:Imagined...re:Engineered...re:Born', '@user', 'soon.', 'Signup', 'to', 'gain', 'access', 'to', 'our', 'beta.', '']
word: ['Vacations', 're', 'Imagined', 're', 'Engineered', 're', 'Born']
Vacations...re:Imagined...re:Engineered...re:Born
word: ['user']
@user
word: ['soon']
soon.
word: ['Signup']
Signup
word: ['to']
to
word: ['gain']
gain
word: ['access']
access
word: ['to']
to
word: ['our']
our
word: ['beta']
beta.
word: []

spl ['Can', 'always', '#countonmother', 'to', 'impart', '#wordsofkindness.', 'Especially', 'on', 'a', 'special', 'day!', '!!', '']
word: ['Can']
Can
word: ['always']
always
word: ['count

In [ ]:
def tok(tweet):
    tokens = []
    unmatchables = []
    x = re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+", tweet)
    url = re.findall(URL, tweet)
    tokens.append(x)
    unmatchables.append(url)
    return (tokens, unmatchables)

In [ ]:
tester = "@user Can U use Smartphone?||http://t.co/Q2WB7riAvK|SmartPhone APP PAYS you!|See-http://t.co/RDlRuGN0iE |Go 2: "
tok(tester)

In [ ]:
x = re.findall("[A-Z]{2,}(?![a-z])|[A-Z][a-z]+(?=[A-Z])|[\'\w\-]+", tester)
y = re.findall(URL, tester)

print(x, y)

for i in x:
    if i in y[0]:
        print("here", i)

In [ ]:
def tokk(line):
    tokens = []
    unmatchables = []
    
    for word in line.split():
        print("w", word)
        if re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+", word) != []:
            x = re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+", word)
            for element in x:
                print("e:", element)
                if element == "âž" or element == "ðŸ":
                    continue
                elif element == "&":
                    tokens.append("and")
                else:
                    tokens.append(element.lower())

        if re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]", word) != [word] and re.findall(r"[^\w|.&!?%#…]+", word) != []:
            unmatchables.append(re.findall(r"[^\w|.!#?%…&]+", word)[0])


    return (tokens, unmatchables)

In [ ]:
tester = "@user Can U use Smartphone? 😘||http://t.co/Q2WB7riAvK|SmartPhone APP PAYS you!|See-http://t.co/RDlRuGN0iE |Go 2: "
tokk(tester)

### Rasmus' ideal tokenizer

In [ ]:
def tokenize_ideal(line):
    tokens = []
    unmatchables = []
    
    for word in line.split():
        #print("w", word)
        if re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+", word) != []:
            x = re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+", word)
            for element in x:
                #print("e:", element)
                if element == "âž" or element == "ðŸ":
                    continue
                elif element == "&":
                    tokens.append("and")
                else:
                    tokens.append(element.lower())

        if re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]", word) != [word] and re.findall(r"[^\w|.&!?%#…]+", word) != []:
            unmatchables.append(re.findall(r"[^\w|.!#?%…&]+", word)[0])


    return (tokens, unmatchables)

### Tokenizer - Hashtags

In [6]:
def tokenizer_hashtag(tweet):
    hashtag_tokens = re.findall(r"#\w+", tweet)
    nomatch_tokens = re.findall(r'^#\w+', tweet)
    #nomatch_tokens = re.findall(r'(?i)(?<=\#)\w+', tweet)
    return hashtag_tokens, nomatch_tokens

In [7]:
# testing with one
tester = "Just walked in to #Starbucks and asked for a tall blonde Hahahaha #irony "
tokenizer_hashtag(tester)

(['#Starbucks', '#irony'], [])

In [ ]:
# for all tweets
for tweet in train_irony["tweets"]:
    print(tokenizer_hashtag(tweet))

### Tokenizer - Upper case (one for all and one for words)

In [ ]:
def tokenizer_uppercase_words(tweet):
    pattern = '[A-Z]+'
    all_char = re.findall(pattern, tweet)
    words = []
    for i in all_char:
        if len(i) > 1:
            words.append(i)
    return words

In [ ]:
for tweet in train_irony["tweets"]:
    print(tokenizer_uppercase_words(tweet))

### TweetTokenizer

In [93]:
text = "Hello, how are you doing ;) Hippedy hoppedity #aintitbubbly -> <--"
TweetTokenizer().tokenize(text)

['Hello',
 ',',
 'how',
 'are',
 'you',
 'doing',
 ';)',
 'Hippedy',
 'hoppedity',
 '#aintitbubbly',
 '->',
 '<--']

In [94]:
tester = "@user Can U use Smartphone?||http://t.co/Q2WB7riAvK|SmartPhone APP PAYS you!|See-http://t.co/RDlRuGN0iE |Go 2: "
TweetTokenizer().tokenize(tester)

['@user',
 'Can',
 'U',
 'use',
 'Smartphone',
 '?',
 '|',
 '|',
 'http://t.co/Q2WB7riAvK|SmartPhone',
 'APP',
 'PAYS',
 'you',
 '!',
 '|',
 'See-http',
 ':/',
 '/',
 't.co/RDlRuGN0iE',
 '|',
 'Go',
 '2',
 ':']

In [ ]:
all_tokens = []

for tweet in train_irony["tweets"]:
    #print(tweet)
    tokens = TweetTokenizer().tokenize(tweet)
    print(tokens)
    
    # adding the counter
    count = Counter(tokens)
    print(count)
    
    for i in tokens:
        all_tokens.append(i)

In [ ]:
all_count = Counter(all_tokens)
all_count

In [ ]:
print("Total vocabulary:", len(all_count))
print("Count of each word:", all_count.most_common())

## Task 2: Characterising Your Data

Characterise the training sets of the two tasks you’ve chosen in terms of elementary corpus statistics: <br>
• Corpus size, vocabulary size, type/token ratio.<br>
• What are the most frequent tokens?<br>
• What types of tokens occur only once, or 2 or 3 times?<br>
• Are there any noticeable differences between your two datasets?<br>
• Are the corpus statistics consistent with Zipf’s law? (no formal test needed, but a plot would be helpful)

### Irony

In [ ]:
irony = train_irony.copy()

Corpus size

In [ ]:
!wc "../datasets/irony/train_text.txt" #-> Prints total number of lines, words and characters.
print("Number of lines, words and character in the training text file for the binary class Irony. \n")

!wc -l "../datasets/irony/train_labels.txt"
print("Number of lines in the training label file for the binary class Irony.")

In [ ]:
all_tokens = []
for tweet in irony["tweets"]:
    #irony_tester["Tokens"] = TweetTokenizer().tokenize(tweet)
    tokens = TweetTokenizer().tokenize(tweet)
    #irony_tester["Tokens"] = tokens
    all_tokens.append(tokens)

irony["tokens"] = all_tokens

In [ ]:
vocabulary_keys = []
vocabulary_count = []

for i in irony["tokens"]:
    vo_c = Counter(i)
    vocabulary_count.append(vo_c)
    vo_k = vo_c.keys()
    vocabulary_keys.append(vo_k)

irony["vocabulary"] = vocabulary_keys

In [ ]:
irony

In [ ]:
# big vocabulary?
bigvocab_keys = []
for i in irony["tokens"]:
    for j in i:
        bigvocab_keys.append(j)

In [ ]:
bag_of_words = sorted(bigvocab_keys)

In [ ]:
vocab_count = Counter(bigvocab_keys)
#vocab_count.keys()
vocab_count
sorted(vocab_count.items(), key=lambda pair: pair[1], reverse=True)

In [ ]:
token_ratio = []

for tok, voca in zip(irony.tokens, irony.vocabulary):
    #print(tokens, vocabularies)
    tok_r = len(voca)/len(tok)
    #print(tok_r)
    token_ratio.append(tok_r)

irony["token_ratio"] = token_ratio

In [ ]:
irony

In [ ]:
# most frequent tokens (5) of each tweet
five_most_common = []

for i in vocabulary_count:
    most_com5 = i.most_common(5)
    five_most_common.append(most_com5)

In [ ]:
five_most_common # vague as many words are unique in the individual tweet

2. Load and tokenise your datasets so that, for each of the corpora, you get a
list of sentences, each sentence represented by a list of tokens. Use the same
tokeniser for all datasets. <br>
http://www.nltk.org/api/nltk.lm.html#module-nltk.lm

In [ ]:
# seeing loaded irony tweets
train_irony

In [ ]:
all_tokens = []
for tweet in train_irony["tweets"]:
    tokens = TweetTokenizer().tokenize(tweet)
    all_tokens.append(tokens)

In [ ]:
train_irony["tokens"] = all_tokens

In [ ]:
train_irony

In [ ]:
bigram_list = []
for i in train_irony["tokens"]:
    bg = list(bigrams(i))
    bigram_list.append(bg)

#bigram_list

bigrams = []

for tweet in bigram_list:
    for bigram in tweet:
        bigram_pr_tweet = []
        for i in bigram:
            bigram_pr_tweet.append([i])
        bigrams.append(bigram_pr_tweet)
#bigrams

In [ ]:
pad_sequence = []

for i in bigram_list:
    heya = list(pad_both_ends(i, n=2))
    pad_sequence.append(heya)

#pad_sequence

In [ ]:
lm = MLE(2)

for i in train_irony["tokens"]:
    train, vocab = padded_everygram_pipeline(2, i)
    fit = lm.fit(train, vocab)
    lookup = lm.vocab.lookup(i)
    print(lookup)

In [ ]:
# making the above as a function to easy change parameter n
def functionwuhu(token_list, n):
    train, vocab = padded_everygram_pipeline(n, token_list)
    lm = MLE(n)
    fit = lm.fit(train, vocab)
    return fit

In [ ]:
testing = functionwuhu(irony_tester["tokens"], 2)
print(testing)

In [ ]:
score_list = []
logscore_list = []

for tweet_tokens in train_irony["tokens"]:
    #for token in tweet_tokens:
    score = lm.score(tweet_tokens)
    score_list.append(score)
    logscore = lm.logscore(tweet_tokens)
    logscore_list.append(logscore)

In [ ]:
for text in train_irony["tokens"]:
    train, vocab = padded_everygram_pipeline(2, text)
    lm = MLE(2)
    fit = lm.fit(train, vocab)

## Task 3: Manual Annotation and Inter-Annotator Agreement
(oh isn't it ironic... don't you think...)

In [8]:
ann_ruben = pd.read_csv("../datasets/annotations/annotations_ruben.csv", header=None, names = ["ann_ruben"])
ann_sabrina = pd.read_csv("../datasets/annotations/annotations_sabrina.csv", header=None, names = ["ann_sabrina"])
ann_rasmus = pd.read_csv("../datasets/annotations/annotations_rasmus.csv", header=None, names = ["ann_rasmus"])
ann_ida = pd.read_csv("../datasets/annotations/annotations_ida.csv", header=None, names = ["ann_ida"])
ann_magnus = pd.read_csv("../datasets/annotations/annotations_magnus.csv", header=None, names = ["ann_magnus"])
ann_truth = pd.read_csv("../datasets/annotations/iaa_labels.txt", header=None, names = ["ann_truth"])

In [17]:
MAA = pd.DataFrame()
MAA["ruben"] = ann_ruben["ann_ruben"]
MAA["sabrina"] = ann_sabrina["ann_sabrina"]
MAA["rasmus"] = ann_rasmus["ann_rasmus"]
MAA["ida"] = ann_ida["ann_ida"]
MAA["magnus"] = ann_magnus["ann_magnus"]
MAA["truth"] = ann_truth["ann_truth"]

In [18]:
for name in MAA.columns:
    score = 0
    for i in MAA.index:
        if MAA[name][i] == MAA['truth'][i]:
            score +=1
    score = round(score/120, 3)
    print(name, score)

ruben 0.675
sabrina 0.675
rasmus 0.708
ida 0.875
magnus 0.542
truth 1.0


In [19]:
rasmus_labels = [("rasmus", i, list(MAA["rasmus"])[i]) for i in range(len(list(MAA["rasmus"])))]
sabrina_labels = [("sabrina", i, list(MAA["sabrina"])[i]) for i in range(len(list(MAA["sabrina"])))]
ruben_labels = [("ruben", i, list(MAA["ruben"])[i]) for i in range(len(list(MAA["ruben"])))]
ida_labels = [("ida", i, list(MAA["ida"])[i]) for i in range(len(list(MAA["ida"])))]
magnus_labels = [("magnus", i, list(MAA["magnus"])[i]) for i in range(len(list(MAA["magnus"])))]
truth_labels = [("truth", i, list(MAA["truth"])[i]) for i in range(len(list(MAA["truth"])))]

ls_w_truth = []
ls_wo_truth = []

for i in range(len(rasmus_labels)):
    ls_w_truth.append(rasmus_labels[i])
    ls_w_truth.append(sabrina_labels[i])
    ls_w_truth.append(ruben_labels[i])
    ls_w_truth.append(ida_labels[i])
    ls_w_truth.append(magnus_labels[i])
    ls_w_truth.append(truth_labels[i])
    ls_wo_truth.append(rasmus_labels[i])
    ls_wo_truth.append(sabrina_labels[i])
    ls_wo_truth.append(ruben_labels[i])
    ls_wo_truth.append(ida_labels[i])
    ls_wo_truth.append(magnus_labels[i])

#### Slavearbejde incoming

In [64]:
ra_sa = []
ra_ru = []
ra_id = []
ra_ma = []
ra_tr = []

for i in range(len(rasmus_labels)):
    ra_sa.append(rasmus_labels[i])
    ra_sa.append(sabrina_labels[i])
    ra_ru.append(rasmus_labels[i])
    ra_ru.append(ruben_labels[i])
    ra_id.append(rasmus_labels[i])
    ra_id.append(ida_labels[i])
    ra_ma.append(rasmus_labels[i])
    ra_ma.append(magnus_labels[i])
    ra_tr.append(rasmus_labels[i])
    ra_tr.append(truth_labels[i])

t_ra_sa = AnnotationTask(data = ra_sa)
print(t_ra_sa.kappa())

t_ra_ru = AnnotationTask(data = ra_ru)
print(t_ra_ru.kappa())

t_ra_id = AnnotationTask(data = ra_id)
print(t_ra_id.kappa())

t_ra_ma = AnnotationTask(data = ra_ma)
print(t_ra_ma.kappa())

t_ra_tr = AnnotationTask(data = ra_tr)
print(t_ra_tr.kappa())

0.5187165775401072
0.40528634361233473
0.39573459715639814
0.015444015444015542
0.40340909090909105


In [63]:
sa_ra = []
sa_ru = []
sa_id = []
sa_ma = []
sa_tr = []

for i in range(len(rasmus_labels)):
    sa_ra.append(rasmus_labels[i])
    sa_ra.append(sabrina_labels[i])
    sa_ru.append(sabrina_labels[i])
    sa_ru.append(ruben_labels[i])
    sa_id.append(sabrina_labels[i])
    sa_id.append(ida_labels[i])
    sa_ma.append(sabrina_labels[i])
    sa_ma.append(magnus_labels[i])
    sa_tr.append(sabrina_labels[i])
    sa_tr.append(truth_labels[i])

t_sa_ra = AnnotationTask(data = sa_ra)
print(t_sa_ra.kappa())

t_sa_ru = AnnotationTask(data = sa_ru)
print(t_sa_ru.kappa())

t_sa_id = AnnotationTask(data = sa_id)
print(t_sa_id.kappa())

t_sa_ma = AnnotationTask(data = sa_ma)
print(t_sa_ma.kappa())

t_sa_tr = AnnotationTask(data = sa_tr)
print(t_sa_tr.kappa())

0.5187165775401072
0.24918389553862905
0.37418513689700117
0.01880621422730981
0.3137829912023461


In [66]:
ru_ra = []
ru_sa = []
ru_id = []
ru_ma = []
ru_tr = []

for i in range(len(rasmus_labels)):
    ru_ra.append(rasmus_labels[i])
    ru_ra.append(ruben_labels[i])
    ru_sa.append(sabrina_labels[i])
    ru_sa.append(ruben_labels[i])
    ru_id.append(ruben_labels[i])
    ru_id.append(ida_labels[i])
    ru_ma.append(ruben_labels[i])
    ru_ma.append(magnus_labels[i])
    ru_tr.append(ruben_labels[i])
    ru_tr.append(truth_labels[i])

t_ru_ra = AnnotationTask(data = ru_ra)
print(t_ru_ra.kappa())

t_ru_sa = AnnotationTask(data = ru_sa)
print(t_ru_sa.kappa())

t_ru_id = AnnotationTask(data = ru_id)
print(t_ru_id.kappa())

t_ru_ma = AnnotationTask(data = ru_ma)
print(t_ru_ma.kappa())

t_ru_tr = AnnotationTask(data = ru_tr)
print(t_ru_tr.kappa())

0.40528634361233473
0.24918389553862905
0.40463065049614094
-0.053227633069082736
0.3518005540166206


In [68]:
id_ra = []
id_sa = []
id_ru = []
id_ma = []
id_tr = []

for i in range(len(rasmus_labels)):
    id_ra.append(rasmus_labels[i])
    id_ra.append(ida_labels[i])
    id_sa.append(sabrina_labels[i])
    id_sa.append(ida_labels[i])
    id_ru.append(ruben_labels[i])
    id_ru.append(ida_labels[i])
    id_ma.append(ida_labels[i])
    id_ma.append(magnus_labels[i])
    id_tr.append(ida_labels[i])
    id_tr.append(truth_labels[i])

t_id_ra = AnnotationTask(data = id_ra)
print(t_id_ra.kappa())

t_id_sa = AnnotationTask(data = id_sa)
print(t_id_sa.kappa())

t_id_ru = AnnotationTask(data = id_ru)
print(t_id_ru.kappa())

t_id_ma = AnnotationTask(data = id_ma)
print(t_id_ma.kappa())

t_id_tr = AnnotationTask(data = id_tr)
print(t_id_tr.kappa())

0.39573459715639814
0.37418513689700117
0.40463065049614094
0.11678115799803723
0.7450424929178471


In [71]:
ma_ra = []
ma_sa = []
ma_ru = []
ma_id = []
ma_tr = []

for i in range(len(rasmus_labels)):
    ma_ra.append(rasmus_labels[i])
    ma_ra.append(magnus_labels[i])
    ma_sa.append(sabrina_labels[i])
    ma_sa.append(magnus_labels[i])
    ma_ru.append(ruben_labels[i])
    ma_ru.append(magnus_labels[i])
    ma_id.append(ida_labels[i])
    ma_id.append(magnus_labels[i])
    ma_tr.append(magnus_labels[i])
    ma_tr.append(truth_labels[i])

t_ma_ra = AnnotationTask(data = ma_ra)
print(t_ma_ra.kappa())

t_ma_sa = AnnotationTask(data = ma_sa)
print(t_ma_sa.kappa())

t_ma_ru = AnnotationTask(data = ma_ru)
print(t_ma_ru.kappa())

t_ma_id = AnnotationTask(data = ma_id)
print(t_ma_id.kappa())

t_ma_tr = AnnotationTask(data = ma_tr)
print(t_ma_tr.kappa())

0.015444015444015542
0.01880621422730981
-0.053227633069082736
0.11678115799803723
0.12466843501326258


In [73]:
tr_ra = []
tr_sa = []
tr_ru = []
tr_id = []
tr_ma = []

for i in range(len(rasmus_labels)):
    tr_ra.append(rasmus_labels[i])
    tr_ra.append(truth_labels[i])
    tr_sa.append(sabrina_labels[i])
    tr_sa.append(truth_labels[i])
    tr_ru.append(ruben_labels[i])
    tr_ru.append(truth_labels[i])
    tr_id.append(ida_labels[i])
    tr_id.append(truth_labels[i])
    tr_ma.append(magnus_labels[i])
    tr_ma.append(truth_labels[i])

t_tr_ra = AnnotationTask(data = tr_ra)
print(t_tr_ra.kappa())

t_tr_sa = AnnotationTask(data = tr_sa)
print(t_tr_sa.kappa())

t_tr_ru = AnnotationTask(data = tr_ru)
print(t_tr_ru.kappa())

t_tr_id = AnnotationTask(data = tr_id)
print(t_tr_id.kappa())

t_tr_ma = AnnotationTask(data = tr_ma)
print(t_tr_ma.kappa())

0.40340909090909105
0.3137829912023461
0.3518005540166206
0.7450424929178471
0.12466843501326258


In [78]:
ra_sum = t_ra_sa.kappa() + t_ra_ru.kappa() + t_ra_id.kappa() + t_ra_ma.kappa() + t_ra_tr.kappa()
sa_sum = t_sa_ra.kappa() + t_sa_ru.kappa() + t_sa_id.kappa() + t_sa_ma.kappa() + t_sa_tr.kappa()
ru_sum = t_ru_ra.kappa() + t_ru_sa.kappa() + t_ru_id.kappa() + t_ru_ma.kappa() + t_ru_tr.kappa()
id_sum = t_id_ra.kappa() + t_id_sa.kappa() + t_id_ru.kappa() + t_id_ma.kappa() + t_id_tr.kappa()
ma_sum = t_ma_ra.kappa() + t_ma_sa.kappa() + t_ma_ru.kappa() + t_ma_id.kappa() + t_ma_tr.kappa()
tr_sum = t_tr_ra.kappa() + t_tr_sa.kappa() + t_tr_ru.kappa() + t_tr_id.kappa() + t_tr_ma.kappa()

total_sum = ra_sum + sa_sum + ru_sum + id_sum + ma_sum + tr_sum
total_sum / 30

0.29228296799333725

In [ ]:
# CHANGE THIS IN MAIN
rasmus_labels = [("rasmus", i, list(MAA["rasmus"])[i]) for i in range(len(list(MAA["rasmus"])))]
sabrina_labels = [("sabrina", i, list(MAA["sabrina"])[i]) for i in range(len(list(MAA["sabrina"])))]
ruben_labels = [("ruben", i, list(MAA["ruben"])[i]) for i in range(len(list(MAA["ruben"])))]
ida_labels = [("ida", i, list(MAA["ida"])[i]) for i in range(len(list(MAA["ida"])))]
magnus_labels = [("magnus", i, list(MAA["magnus"])[i]) for i in range(len(list(MAA["magnus"])))]
truth_labels = [("truth", i, list(MAA["truth"])[i]) for i in range(len(list(MAA["truth"])))]

ls_w_truth = []
ls_wo_truth = []

for i in range(len(rasmus_labels)):
    ls_w_truth.append(sabrina_labels[i])
    ls_w_truth.append(rasmus_labels[i])
    ls_w_truth.append(ruben_labels[i])
    ls_w_truth.append(ida_labels[i])
    ls_w_truth.append(magnus_labels[i])
    ls_w_truth.append(truth_labels[i])
    ls_wo_truth.append(sabrina_labels[i])
    ls_wo_truth.append(rasmus_labels[i])
    ls_wo_truth.append(ruben_labels[i])
    ls_wo_truth.append(ida_labels[i])
    ls_wo_truth.append(magnus_labels[i])

In [150]:
# CHANGE THIS IN MAIN

names = [i for i in MAA.columns]
list_of_labels = [sabrina_labels, rasmus_labels, ruben_labels, ida_labels, magnus_labels, truth_labels]

total_sum = 0
for i, name in enumerate(names):
    print("\n name:", name)
    current = list_of_labels[i]
    #print(current)
    for idx in range(len(names)):
        if idx != i:
            ls = []
            pair_with_name = names[idx]
            pair_with = list_of_labels[idx]
            for annotation in range(len(current)):
                ls.append(current[annotation])
                ls.append(pair_with[annotation])
            #print(ls)
            t = AnnotationTask(data = ls)
            print(names[idx], t.kappa())
            total_sum += t.kappa()

print("\nAverage kappa:", total_sum/30)


 name: ruben
sabrina 0.24918389553862905
rasmus 0.40528634361233473
ida 0.40463065049614094
magnus -0.053227633069082736
truth 0.3518005540166206

 name: sabrina
ruben 0.24918389553862905
rasmus 0.5187165775401072
ida 0.37418513689700117
magnus 0.01880621422730981
truth 0.3137829912023461

 name: rasmus
ruben 0.40528634361233473
sabrina 0.5187165775401072
ida 0.39573459715639814
magnus 0.015444015444015542
truth 0.40340909090909105

 name: ida
ruben 0.40463065049614094
sabrina 0.37418513689700117
rasmus 0.39573459715639814
magnus 0.11678115799803723
truth 0.7450424929178471

 name: magnus
ruben -0.053227633069082736
sabrina 0.01880621422730981
rasmus 0.015444015444015542
ida 0.11678115799803723
truth 0.12466843501326258

 name: truth
ruben 0.3518005540166206
sabrina 0.3137829912023461
rasmus 0.40340909090909105
ida 0.7450424929178471
magnus 0.12466843501326258

Average kappa: 0.2922829679933372


In [27]:
t_w_truth = AnnotationTask(data = ls_w_truth)
print("Average observed agreement:", t_w_truth.avg_Ao())
print("S score:", t_w_truth.S())
print("Scott's multi-pi score:", t_w_truth.pi())
print("Cohen's kappa score:", t_w_truth.kappa())
print("Fleiss' multi-kappa score:", t_w_truth.multi_kappa())

Average observed agreement: 0.6327777777777777
S score: 0.2655555555555553
Scott's multi-pi score: 0.25771459319509304
Cohen's kappa score: 0.2922829679933372
Fleiss' multi-kappa score: 0.27701618783724646


In [50]:
for i in range(len(rasmus_labels)):
    print("i:", i)
    for name in MAA.columns:
        print("name", name)
        ls = []
        print("MAA[name][i]:", MAA[name][i])
        ls.append(MAA[name][i])
        print(ls)

i: 0
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 1
[1]
name rasmus
MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 1
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 2
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 3
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 0
[0]
name truth
MAA[name][i]: 0
[0]
i: 4
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 5
name ruben
MAA[name][i]: 1
[1]

MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 0
[0]
i: 50
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 1
[1]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 51
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 0
[0]
i: 52
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 53
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 1
[1]
name rasmus
MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 0
[0]
name truth
MAA[name][i]: 1
[1]
i: 54
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnu

MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 97
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 0
[0]
i: 98
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 0
[0]
i: 99
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 1
[1]
name rasmus
MAA[name][i]: 1
[1]
name ida
MAA[name][i]: 1
[1]
name magnus
MAA[name][i]: 1
[1]
name truth
MAA[name][i]: 1
[1]
i: 100
name ruben
MAA[name][i]: 1
[1]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida
MAA[name][i]: 0
[0]
name magnus
MAA[name][i]: 0
[0]
name truth
MAA[name][i]: 0
[0]
i: 101
name ruben
MAA[name][i]: 0
[0]
name sabrina
MAA[name][i]: 0
[0]
name rasmus
MAA[name][i]: 0
[0]
name ida

In [31]:
t_w_truth = AnnotationTask(data = ls_w_truth)

for name in MAA.columns:
    for i in ls_w_truth:
        if i[0] == name:
            continue
        else: 
            k = t_w_truth.kappa()
            print(k)
    print(new)
    print(name)

[('rasmus', 0, 1), ('sabrina', 0, 1), ('ida', 0, 1), ('magnus', 0, 1), ('truth', 0, 1), ('rasmus', 1, 0), ('sabrina', 1, 0), ('ida', 1, 0), ('magnus', 1, 1), ('truth', 1, 1), ('rasmus', 2, 1), ('sabrina', 2, 0), ('ida', 2, 1), ('magnus', 2, 1), ('truth', 2, 1), ('rasmus', 3, 0), ('sabrina', 3, 0), ('ida', 3, 0), ('magnus', 3, 0), ('truth', 3, 0), ('rasmus', 4, 1), ('sabrina', 4, 0), ('ida', 4, 1), ('magnus', 4, 1), ('truth', 4, 1), ('rasmus', 5, 1), ('sabrina', 5, 0), ('ida', 5, 1), ('magnus', 5, 0), ('truth', 5, 1), ('rasmus', 6, 0), ('sabrina', 6, 0), ('ida', 6, 0), ('magnus', 6, 1), ('truth', 6, 0), ('rasmus', 7, 0), ('sabrina', 7, 0), ('ida', 7, 1), ('magnus', 7, 1), ('truth', 7, 1), ('rasmus', 8, 1), ('sabrina', 8, 1), ('ida', 8, 1), ('magnus', 8, 0), ('truth', 8, 1), ('rasmus', 9, 0), ('sabrina', 9, 0), ('ida', 9, 0), ('magnus', 9, 1), ('truth', 9, 0), ('rasmus', 10, 1), ('sabrina', 10, 1), ('ida', 10, 0), ('magnus', 10, 1), ('truth', 10, 0), ('rasmus', 11, 1), ('sabrina', 11, 0)

In [36]:
for name in MAA.columns:
    print(name)
    t_w_truth = AnnotationTask(data = ls_w_truth)
    k = t_w_truth.kappa()
    print(k)

ruben
0.2922829679933372
sabrina
0.2922829679933372
rasmus
0.2922829679933372
ida
0.2922829679933372
magnus
0.2922829679933372
truth
0.2922829679933372


In [13]:
# https://www.nltk.org/api/nltk.metrics.html

# making the (‘c1’, ‘1’, ‘v1’) kind of set up of the annotations
all_list = []

for name in annotations.columns:
    for i in annotations.index:
        li = (name, i, annotations[name][i])
        all_list.append(li)

# So far only made it work with taking all indices for each name at a time and not for each index all names
# does that make a difference? who knows

#all_list

In [14]:
t = AnnotationTask(data = all_list)
print("Average observed agreement: ", t.avg_Ao())
print("Pi: ", t.pi())
print("Cohen's Kappa: ", t.kappa())
print("Fleiss' Kappa: ", t.multi_kappa())
print(t.S())

Average observed agreement:  0.6327777777777777
Pi:  0.25771459319509304
Cohen's Kappa:  0.2922829679933372
Fleiss' Kappa:  0.27701618783724646
0.2655555555555553


We really be bad at annotating irony, man...

#### Confusion matrix for each annotator

In [15]:
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.confusion_matrix.html

y_true = annotations["truth"]

for name in annotations.columns:
    print(name, "\n", confusion_matrix(y_true, annotations[name]), "\n")

print("[[""non-irony labelled non-irony - non-irony labelled irony""]", "\n", "[ irony labelled non-irony - irony labelled irony]]")


ruben 
 [[42 23]
 [16 39]] 

sabrina 
 [[62  3]
 [36 19]] 

rasmus 
 [[53 12]
 [23 32]] 

ida 
 [[62  3]
 [12 43]] 

magnus 
 [[18 47]
 [ 8 47]] 

truth 
 [[65  0]
 [ 0 55]] 

[[non-irony labelled non-irony - non-irony labelled irony] 
 [ irony labelled non-irony - irony labelled irony]]


In [ ]:
# Pair-wise Cohen Kappa scores for annotator pairs and the group Fleiss Kappa score for group 1.


In [16]:
for name in annotations.columns:
    t = AnnotationTask(data = )
    print(name, "\n", confusion_matrix(y_true, annotations[name]), "\n")
    
t = AnnotationTask(data = all_list)
print("Average observed agreement: ", t.avg_Ao())
print("Pi: ", t.pi())
print("Cohen's Kappa: ", t.kappa())
print("Fleiss' Kappa: ", t.multi_kappa())
print(t.S())

ruben 
 [[42 23]
 [16 39]] 

sabrina 
 [[62  3]
 [36 19]] 

rasmus 
 [[53 12]
 [23 32]] 

ida 
 [[62  3]
 [12 43]] 

magnus 
 [[18 47]
 [ 8 47]] 

truth 
 [[65  0]
 [ 0 55]] 



## Task 4: Automatic Prediction

## Classifiers

In [ ]:
# https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.CountVectorizer.html

In [ ]:
print(X.toarray())

In [ ]:
corpus = []

for i in train_irony["tweets"]:
    corpus.append(i)

vectorizer = CountVectorizer()
X_train_counts = vectorizer.fit_transform(corpus)
print(vectorizer.get_feature_names())

In [ ]:
corpus

In [ ]:
something = X_train_counts.toarray()
something.shape

In [ ]:
unique, frequency = np.unique(something, return_counts = True)
# print unique values array
print("Unique Values:", unique)
# print frequency array
print("Frequency Values:", frequency)

In [ ]:
# SAME WITH N-GRAMS
vectorizer2 = CountVectorizer(analyzer='word', ngram_range=(2, 2))
X2 = vectorizer2.fit_transform(corpus)
print(vectorizer2.get_feature_names())

In [ ]:
some = X2.toarray()
some

In [ ]:
unique, frequency = np.unique(some, return_counts = True)
# print unique values array
print("Unique Values:", unique)
# print frequency array
print("Frequency Values:", frequency)

In [ ]:
tf_transformer = TfidfTransformer(use_idf=False).fit(X)
X_train_tf = tf_transformer.transform(X)
print(X_train_tf)

In [ ]:
print(X_train_tf.shape)

In [ ]:
clf = MultinomialNB().fit(X_train_tf, twenty_train.target)

In [ ]:
Y = train_irony_labels["1"]

In [ ]:
ls = []
for i in train_irony_labels["labels"]:
    ls.append(i)

### More sklearn

In [ ]:
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.recall_score.html
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.confusion_matrix.html
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.multilabel_confusion_matrix.html#sklearn.metrics.multilabel_confusion_matrix
# https://scikit-learn.org/stable/modules/generated/sklearn.metrics.precision_score.html#sklearn.metrics.precision_score

In [ ]:
# BAG OF WORDS

bigvocab_keys = []
for i in train_irony["tokens"]:
    for j in i:
        bigvocab_keys.append(j)

bag_of_words = sorted(bigvocab_keys)
bag_of_words

# FOLLOW-ALONG

In [ ]:
# following this https://scikit-learn.org/stable/tutorial/text_analytics/working_with_text_data.html

count_vect = CountVectorizer()
X_train_counts = count_vect.fit_transform(corpus)
X_train_counts.shape

In [ ]:
tf_transformer = TfidfTransformer(use_idf=False).fit(X_train_counts)
X_train_tf = tf_transformer.transform(X_train_counts)
X_train_tf.shape

In [ ]:
tfidf_transformer = TfidfTransformer()
X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)
X_train_tfidf.shape

In [ ]:
clf = MultinomialNB().fit(X_train_tfidf, ls)

In [ ]:
text_clf = Pipeline([
    ('vect', CountVectorizer()),
    ('tfidf', TfidfTransformer()),
    ('clf', MultinomialNB()),
])

In [ ]:
text_clf.fit(corpus, ls)

In [ ]:
docs_test = test_irony
predicted = text_clf.predict(docs_test)
np.mean(predicted == test_irony_labels)

In [ ]:
from sklearn.linear_model import SGDClassifier

text_clf = Pipeline([
    ('vect', CountVectorizer()),
    ('tfidf', TfidfTransformer()),
    ('clf', SGDClassifier(loss='hinge', penalty='l2',
                          alpha=1e-3, random_state=42,
                          max_iter=5, tol=None)),
])

text_clf.fit(corpus, ls)

predicted = text_clf.predict(docs_test)
np.mean(predicted == test_irony_labels)

In [ ]:
predicted = text_clf.predict(docs_test)
np.mean(predicted == test_irony_labels)

# GET AT IT

### SGD Classifier

In [ ]:
train_corpus1 = []
test_corpus1 = []

for tweet in train_irony["tweets"]:
    tokens = TweetTokenizer().tokenize(tweet)
    train_corpus1.append(tokens[0])

for tweet in test_irony["tweets"]:
    tokens = TweetTokenizer().tokenize(tweet)
    test_corpus1.append(tokens[0])

In [ ]:
irony_clf = Pipeline([('vect', CountVectorizer()), ('tfidf', TfidfTransformer()), ('clf', SGDClassifier(loss='log'))])
irony_clf.fit(train_corpus1, train_irony_labels["labels"])

In [ ]:
predicted = irony_clf.predict(test_corpus1)
print(np.mean(predicted == test_irony_labels["labels"]))

In [ ]:
confusion_matrix(test_irony_labels["labels"], predicted)
# seems to label a lot of non-irony as irony. Overlabelling irony in general

In [ ]:
train_corpus2 = []
test_corpus2 = []

for tweet in train_irony["tweets"]:
    tokens = re.findall("[\w']+", tweet)
    train_corpus2.append(tokens[0])

for tweet in test_irony["tweets"]:
    tokens = re.findall("[\w']+", tweet)
    test_corpus2.append(tokens[0])

In [ ]:
clf2 = Pipeline([('vect', CountVectorizer()), ('tfidf', TfidfTransformer()), ('clf', SGDClassifier(loss='log'))])
clf2.fit(train_corpus2, train_irony_labels["labels"])

In [ ]:
predicted2 = clf2.predict(test_corpus2)
print(np.mean(predicted == test_irony_labels["labels"]))

In [ ]:
confusion_matrix(test_irony_labels["labels"], predicted2)
# predicts 50/50 non-irony as irony or non-irony

In [ ]:
print(classification_report(test_irony_labels["labels"], predicted2, target_names = irony_mapping["label"]))

### SVC Classifier
https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html

### MLP Classifier
https://scikit-learn.org/stable/modules/generated/sklearn.neural_network.MLPClassifier.html

In [ ]:
from sklearn.neural_network import MLPClassifier
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split

X, y = make_classification(n_samples=len(train_irony["tweets"]), random_state=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=1)
clf = MLPClassifier(random_state=1, max_iter=300).fit(X_train, y_train)

In [ ]:
clf.predict_proba(X_test[:1])

clf.predict(X_test[:5, :])

clf.score(X_test, y_test)

### Decision Tree Classifier
https://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html

# new tokenizer

In [50]:
# useful regex

word = r"\w+"
emoji = "[\U00010000-\U0010ffff]"

test = "hello, how are you doing? http://t.co/Q2WB7riAvK"
x = re.findall(word, test)

# PROBLEM, CAN'T JUST APPEND EVERY WORD, AS IT SPLITS AT EVERYTHING AND THEREFORE INCLUDES THE LINKSHIT

test.split()

['hello,', 'how', 'are', 'you', 'doing?', 'http://t.co/Q2WB7riAvK']

In [51]:
def final_countdown(tweet):
    tokens = []
    unmatchables = []
    x_emoji = re.findall(emoji, tweet)
    tokens.append(x_emoji)
    hashtagged_word = "^#" # starts with
    x = re.findall(word, tweet)
    tokens.append(x)
    hash_x = re.search(hashtagged_word, tweet)
    if hash_x:
        tokens.append(tweet)
    return (tokens, unmatchables)
    
SUP = []
for tweet in train_irony["tweets"]:
    print("Original tweet: ", tweet)
    sup = final_countdown(tweet)
    SUP.append(sup)

Original tweet:  seeing ppl walking w/ crutches makes me really excited for the next 3 weeks of my life  
Original tweet:  look for the girl with the broken smile, ask her if she wants to stay while, and she will be loved. 💕🎵 
Original tweet:  Now I remember why I buy books online @user #servicewithasmile  
Original tweet:  @user @user So is he banded from wearing the clothes?  #Karma 
Original tweet:  Just found out there are Etch A Sketch apps.  #oldschool #notoldschool 
Original tweet:  Hey what do you know, one of the witnesses supporting Darren Wilson's story lied! And is racist! Mind blown!  
Original tweet:  @user on stage at #flzjingleball at the @user in #Tampa #iheartradio 
Original tweet:  You know it's going to be a great day when you're Garmin resets itself and you spill some cinnamon down yourself  #slowclap 
Original tweet:  Halfway thorough my workday ... Woooo  
Original tweet:  Would like to thank my nephew for giving me his horrible cold & sore throat etc.. Much appr

Original tweet:  @user @user How can you even keep up with all this great music?! 
Original tweet:  Getting my shit together in 2015 like........ #2015isthenewturnup #myboos #funtimes #makingmemories... 
Original tweet:  wow, look at you hotshot.  #isthatajoke 
Original tweet:  @user definitely consult a tax professional on that one. 
Original tweet:  What a joke. Thanks for the detailed response and communication with your customers.  @user @user 
Original tweet:  Oh noes! The night train Berlin-Malmö runs only during summer! & me who was planning a long comfortable train trip :( 
Original tweet:  When j need the mailman to come late, he's here at 8a. When I can't wait for the mail to come? 7p.  
Original tweet:  Don't forget the true meaning of Christmas🙏 
Original tweet:  #page#found#404 
Original tweet:  I just swallowed my giant lozenge. Now my throat actually hurts. I'm glad I have Twitter to share my despair. #sick 
Original tweet:  @user not always. They've found them in $500k 

Original tweet:  @user @user @user And it starts :P |#GetEnchanted 
Original tweet:  3 hours sleep yay loving life  
Original tweet:  @user try your luck tom! You can be one of the 20 free passers and makatanggap ng free item from david. Okay na yun tas uwi haha 
Original tweet:  #TeenAnalCasting #What What is the Creampie Crusade? 
Original tweet:  Everyones full of ruddy xmas cheer here  
Original tweet:  home alone aka turn on all the lights #scaredycat 
Original tweet:  @user @user in the paper that supported the blackshirts.  
Original tweet:  nope, you do NOT fit that definition @user @user @user @user @user 
Original tweet:  @user @user @user You are kidding, right?  #poortaste 
Original tweet:   so Ugly Christmas Sweater Women's Sz M 
Original tweet:  I love when I'm taken as a joke...makes me feel so good about myself!  
Original tweet:  Wow Tim Hortons Cobourg is really on their A game today  
Original tweet:  It was so incredible to hear Justice Ginsburg speak today. She tru

Original tweet:  big up @user 4 ur post When cunts run through your photos😒 #its#a#struggle#its#a#problem check da n... 
Original tweet:  @user Sig-ni-fi-cant witter  
Original tweet:  Check out my new post! MyFairDaily: 10 Things I've Been Loving Lately #lbloggers #holidays #myfairdaily #favorites 
Original tweet:  It's not possible to have enough time 
Original tweet:  @user you wearing the pin I sent for the rest of the video yesterday made my day. #daymade #addicted 
Original tweet:  Climate change redux: CALIFORNIANS experience drought & voted for bonds to cover.Climate changed &now we have most rain in 100 years.  
Original tweet:   Putin praising Constitutional Court for defending against 'arbitrary action on the part of the government 
Original tweet:  Perfect time to get really sick  😫😷 
Original tweet:  Jordan fan here|| 😛 -not a hater. 
Original tweet:  #All #Cute #Dude #Girlygirl #I039m #Into #Is |Please RT: 
Original tweet:  Hey, @user DenialCSGO decided that they want to 

In [52]:
SUP

[([[],
   ['seeing',
    'ppl',
    'walking',
    'w',
    'crutches',
    'makes',
    'me',
    'really',
    'excited',
    'for',
    'the',
    'next',
    '3',
    'weeks',
    'of',
    'my',
    'life']],
  []),
 ([['💕', '🎵'],
   ['look',
    'for',
    'the',
    'girl',
    'with',
    'the',
    'broken',
    'smile',
    'ask',
    'her',
    'if',
    'she',
    'wants',
    'to',
    'stay',
    'while',
    'and',
    'she',
    'will',
    'be',
    'loved']],
  []),
 ([[],
   ['Now',
    'I',
    'remember',
    'why',
    'I',
    'buy',
    'books',
    'online',
    'user',
    'servicewithasmile']],
  []),
 ([[],
   ['user',
    'user',
    'So',
    'is',
    'he',
    'banded',
    'from',
    'wearing',
    'the',
    'clothes',
    'Karma']],
  []),
 ([[],
   ['Just',
    'found',
    'out',
    'there',
    'are',
    'Etch',
    'A',
    'Sketch',
    'apps',
    'oldschool',
    'notoldschool']],
  []),
 ([[],
   ['Hey',
    'what',
    'do',
    'you',
   

In [ ]:
def tokenize_ideal(line):
    tokens = []
    unmatchables = []
    re1 = r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+"
    
    for word in line.split():
        if re.findall(re1, word) != []:
            x = re.findall(re1, word)
            for element in x:
                if element == "âž" or element == "ðŸ":
                    continue
                elif element == "&":
                    tokens.append("and")
                else:
                    tokens.append(element.lower())

        if re.findall(r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]", word) != [word] and re.findall(r"[^\w|.&!?%#…]+", word) != []:
            unmatchables.append(re.findall(r"[^\w|.!#?%…&]+", word)[0])


    return (tokens, unmatchables)

In [53]:
SUP = []
for i in train_irony["tweets"]:
    sup = tokenize_ideal(i)
    SUP.append(sup)

NameError: name 'tokenize_ideal' is not defined

In [54]:
SUP

[]

In [55]:
hashtags = []
for tweet in train_irony["tweets"]:
    hashtag_tokens = re.findall(r"#(\w+)", tweet)
    hashtags.append(hashtag_tokens)

not_hashtag = []
for tweet in train_irony["tweets"]:
    if i not in hashtag_tokens:
        not_hashtag.append(i)

In [57]:
hashtags

[]

In [62]:
# WORKING PROGRESS

# Get rid of links, @user
# Preserve words, hashtagged words

unmatchable = []
tokens = []
for i in train_irony["tweets"]:
    #next = i.split("|")
    url = re.findall('([\w\-\.]+)://([\w\-\.]+)/(\w+).(\w+)', i)
    at = re.findall(r"@(\w+)", i)
    unmatchable.append(url)
    unmatchable.append(at)
    
    hashtags = re.findall(r"#(\w+)", i)
    tokens.append(hashtags)
    
    for i in hashtags:
        lala = re.sub(r'\b'+i+r'\b(?!@)', '#'+i, i)
        tokens.append(lala)

In [63]:
tokens

[[],
 [],
 ['servicewithasmile'],
 '#servicewithasmile',
 ['Karma'],
 '#Karma',
 ['oldschool', 'notoldschool'],
 '#oldschool',
 '#notoldschool',
 [],
 ['flzjingleball', 'Tampa', 'iheartradio'],
 '#flzjingleball',
 '#Tampa',
 '#iheartradio',
 ['slowclap'],
 '#slowclap',
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 ['POPCORN'],
 '#POPCORN',
 ['WalkingDead'],
 '#WalkingDead',
 ['feeling', 'this'],
 '#feeling',
 '#this',
 [],
 ['barber', 'hairdresser', 'blondie'],
 '#barber',
 '#hairdresser',
 '#blondie',
 [],
 ['workout', 'motivation', 'fitfam'],
 '#workout',
 '#motivation',
 '#fitfam',
 [],
 ['GoodellMustGo'],
 '#GoodellMustGo',
 [],
 [],
 [],
 [],
 [],
 ['justkiddingIlovethem'],
 '#justkiddingIlovethem',
 ['productivity', 'tumblr'],
 '#productivity',
 '#tumblr',
 ['slowinternet'],
 '#slowinternet',
 [],
 [],
 ['lowbudget', 'smartmove', 'a', 'good', 'idea', 'butscheming'],
 '#lowbudget',
 '#smartmove',
 '#a',
 '#good',
 '#idea',
 '#butscheming',
 ['fml'],
 '#fml',
 ['LOL', 'Respect

In [ ]:
for i in train_irony["tweets"]:
    print(i)

In [ ]:
hashtag_tokens = re.findall(r"#(\w+)", tweet)

In [ ]:
def hashtag_tokenizer(tweet):
    tokens = []
    unmatchables = []
    
    for word in tweet.split():
        hashtag = re.findall(r'#(\w+)', word)
        if len(hashtag) != 0:
            tokens.append(hashtag[0])
        
        all_words = re.findall(r'\w+', word)
        for word in all_words:
            if word not in hashtags:
                unmatchables.append(word)
    
    return tokens, unmatchables

In [ ]:
test_string = "Trying to write something ironic on command is kind of #ironic #likethesong"
hashtag_tokenizer(test_string)

In [ ]:
for i in hashtag_tokenizer(test_string)[0]:
    if i in hashtag_tokenizer(test_string)[1]:
        print(i, "here")

In [ ]:
test = []
for i in train_irony["tweets"]:
    test.append(hashtag_tokenizer(i))

In [ ]:
test

In [79]:
tester = "hello, how are you, I'm feeling #super #duper #good"
re.findall("#\w+", tester)

['#super', '#duper', '#good']

# Checking for equality in test data
If that even matters?

#### Irony (binary)

In [ ]:
t_irony_df = test_irony.copy()
t_irony_df["labels"] = test_irony_labels["labels"]
print(t_irony_df["labels"].value_counts())

irony_0 = t_irony_df.loc[t_irony_df['labels'] == 0]
irony_1 = t_irony_df.loc[t_irony_df['labels'] == 1]

print("Original amount of 0 and 1 values in irony: ", (len(irony_0), len(irony_1)))
# more 0 than 1, meaning we adjust the 0-values to the 1-values

irony_len = len(irony_0)
irony_1 = irony_1[:irony_len]

print("Adjusted amount of 0 and 1 values in irony: ", (len(irony_0), len(irony_1)))

In [ ]:
balanced_test_irony = irony_0.append(irony_1)

#### Abortion (multiclass)

In [ ]:
t_abor_df = test_abortion.copy()
t_abor_df["labels"] = test_abortion_labels["labels"]
print(t_abor_df["labels"].value_counts())

zero = t_abor_df.loc[t_abor_df['labels'] == 0]
one = t_abor_df.loc[t_abor_df['labels'] == 1]
two = t_abor_df.loc[t_abor_df['labels'] == 2]

print("Original amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))
# the least amount of 0-values, meaning we adjust the 1- and 2-values to the 0-values

abor_len = len(zero)
one = one[:abor_len]
two = two[:abor_len]

print("Adjusted amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))

In [ ]:
balanced_test_abortion = zero.append(one)
balanced_test_abortion = balanced_test_abortion.append(two)

#### Atheism (multiclass)

In [ ]:
t_ath_df = test_atheism.copy()
t_ath_df["labels"] = test_atheism_labels["labels"]
print(t_ath_df["labels"].value_counts())

zero = t_ath_df.loc[t_ath_df['labels'] == 0]
one = t_ath_df.loc[t_ath_df['labels'] == 1]
two = t_ath_df.loc[t_ath_df['labels'] == 2]

print("Original amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))
# the least amount of 0-values, meaning we adjust the 1- and 2-values to the 0-values

ath_len = len(zero)
one = one[:ath_len]
two = two[:ath_len]

print("Adjusted amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))

In [ ]:
balanced_test_atheism = zero.append(one)
balanced_test_atheism = balanced_test_atheism.append(two)

#### Climate (multiclass)

In [ ]:
t_cli_df = test_climate.copy()
t_cli_df["labels"] = test_climate_labels["labels"]
print(t_cli_df["labels"].value_counts())

zero = t_cli_df.loc[t_cli_df['labels'] == 0]
one = t_cli_df.loc[t_cli_df['labels'] == 1]
two = t_cli_df.loc[t_cli_df['labels'] == 2]

print("Original amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))
# the least amount of 1-values, meaning we adjust the 0- and 2-values to the 0-values

cli_len = len(one)
zero = one[:cli_len]
two = two[:cli_len]

print("Adjusted amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))

In [ ]:
balanced_test_climate = one.append(zero)
balanced_test_climate = balanced_test_climate.append(two)

#### Feminist (multiclass)

In [ ]:
t_fem_df = test_feminist.copy()
t_fem_df["labels"] = test_feminist_labels["labels"]
print(t_fem_df["labels"].value_counts())

zero = t_fem_df.loc[t_fem_df['labels'] == 0]
one = t_fem_df.loc[t_fem_df['labels'] == 1]
two = t_fem_df.loc[t_fem_df['labels'] == 2]

print("Original amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))
# the least amount of 0-values, meaning we adjust the 1- and 2-values to the 0-values

fem_len = len(zero)
one = zero[:fem_len]
two = one[:fem_len]

print("Adjusted amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))

In [ ]:
balanced_test_feminist = zero.append(one)
balanced_test_feminist = balanced_test_feminist.append(two)

#### Hillary (multiclass)

In [ ]:
t_hill_df = test_hillary.copy()
t_hill_df["labels"] = test_hillary_labels["labels"]
print(t_hill_df["labels"].value_counts())

zero = t_hill_df.loc[t_hill_df['labels'] == 0]
one = t_hill_df.loc[t_hill_df['labels'] == 1]
two = t_hill_df.loc[t_hill_df['labels'] == 2]

print("Original amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))
# the least amount of 2-values, meaning we adjust the 0- and 1-values to the 2-values

hill_len = len(two)
zero = zero[:hill_len]
one = one[:hill_len]

print("Adjusted amount of 0 and 1 values in hillary: ", (len(zero), len(one), len(two)))

In [ ]:
balanced_test_hillary = two.append(one)
balanced_test_hillary = balanced_test_hillary.append(zero)

# Something new... And hopefully excisting

In [95]:
import re
re.findall(r"[\w']+|[.,!?;]", "Hello, I'm a string!")
'Hello', ',', "I'm", 'a', 'string', '!'

('Hello', ',', "I'm", 'a', 'string', '!')

In [ ]:
# https://blog.finxter.com/how-to-extract-all-emojis-from-text-in-python/

In [171]:
tester = train_irony["tweets"][18]
tester

first = re.findall(r"[\w']+ | [.,!?;] | #\w+", tester)
print(first)
second = re.findall(r'[^\w\s,.]', tester)
print(second)

[' #POPCORN', 'bringing ', 'this ', 'at ', 'movie ', 'tuesday ']
['🙀', '😱', '🙀', '😱', '🙀', '😱', '#', '!', '!', '!', '!', '!', '!', '😂', '🎅', '😂', '🎅', '😂', '🔫', '🔫', '!', '!']


In [176]:
for i in train_irony["tweets"]:
    print(i)
    hello = re.findall(r"[\w']+ | \w+ | [.,!?;] | #\w+", i)
    print(hello)

seeing ppl walking w/ crutches makes me really excited for the next 3 weeks of my life  
['seeing ', 'ppl ', 'walking ', ' crutches ', 'makes ', 'me ', 'really ', 'excited ', 'for ', 'the ', 'next ', '3 ', 'weeks ', 'of ', 'my ', 'life ']
look for the girl with the broken smile, ask her if she wants to stay while, and she will be loved. 💕🎵 
['look ', 'for ', 'the ', 'girl ', 'with ', 'the ', 'broken ', ' ask ', 'her ', 'if ', 'she ', 'wants ', 'to ', 'stay ', ' and ', 'she ', 'will ', 'be ']
Now I remember why I buy books online @user #servicewithasmile  
['Now ', 'I ', 'remember ', 'why ', 'I ', 'buy ', 'books ', 'online ', 'user ', 'servicewithasmile ']
@user @user So is he banded from wearing the clothes?  #Karma 
['user ', 'user ', 'So ', 'is ', 'he ', 'banded ', 'from ', 'wearing ', 'the ', ' #Karma']
Just found out there are Etch A Sketch apps.  #oldschool #notoldschool 
['Just ', 'found ', 'out ', 'there ', 'are ', 'Etch ', 'A ', 'Sketch ', ' #oldschool', ' #notoldschool']
Hey w

Photo: Abstract Tribal Bubble Jumpsuit Size: s-xl Cost:$39.99 
[' Abstract ', 'Tribal ', 'Bubble ', 'Jumpsuit ', 'xl ', '99 ']
Rain and sleet hun? Yeah I totally want to get dress and go to work. Sounds like  fun  #iwannagobacktobed 
['Rain ', 'and ', 'sleet ', ' Yeah ', 'I ', 'totally ', 'want ', 'to ', 'get ', 'dress ', 'and ', 'go ', 'to ', ' Sounds ', 'like ', ' fun ', ' #iwannagobacktobed']
My professors moustache is so uneven, Mohstash would be ashamed right now 
['My ', 'professors ', 'moustache ', 'is ', 'so ', ' Mohstash ', 'would ', 'be ', 'ashamed ', 'right ', 'now ']
Best Christmas gift @user new album. 
['Best ', 'Christmas ', 'gift ', 'user ', 'new ']
my life won't be complete until I meet @user 💕 
['my ', 'life ', "won't ", 'be ', 'complete ', 'until ', 'I ', 'meet ', 'user ']
If this year wld be filled w all these rainy days it wont be so cool a cool way to start e year 
['If ', 'this ', 'year ', 'wld ', 'be ', 'filled ', 'w ', 'all ', 'these ', 'rainy ', 'days ', 'it '

['user ', 'my ', 'favourite ', 'day ', 'of ', 'the ', 'year ']
Hahaha! @user enjoying the #selfiestick I got her for Christmas! 
['user ', 'enjoying ', 'the ', 'selfiestick ', 'I ', 'got ', 'her ', 'for ']
Love working and be exhausted all the time  
['Love ', 'working ', 'and ', 'be ', 'exhausted ', 'all ', 'the ', 'time ']
Yep, it's exactly what you're thinking... someone called an Ambulance for the former Audi R8...||#Audi #R8 #Carporn  
["it's ", 'exactly ', 'what ', "you're ", ' someone ', 'called ', 'an ', 'Ambulance ', 'for ', 'the ', 'former ', 'Audi ', 'Audi ', 'R8 ', 'Carporn ']
@user Your opinions don't affect me. I'm going to keep living my life. 
['user ', 'Your ', 'opinions ', "don't ", 'affect ', "I'm ", 'going ', 'to ', 'keep ', 'living ', 'my ']
 : #BlackOnBlackCrime comitted by|#BlackLivesMatter #Protest in #FERGUSON ?|http://t.co/SEPGzy9Bzb|Post RTs @user 
[' #BlackOnBlackCrime', ' comitted ', 'BlackLivesMatter ', 'Protest ', 'in ', 'FERGUSON ', 'Post ', 'RTs ', 'use

['user ', 'you ', "didn't ", 'make ', 'enough ', 'of ', 'a ', 'blót ', 'to ', 'Ullr ', 'God ', 'of ', ' and ', 'I ', 'assume ']
Me: my stomach is upset.| My stomach: I AM MORE THAN UPSET!  
[' my ', 'stomach ', 'is ', ' My ', ' I ', 'AM ', 'MORE ', 'THAN ']
Yay time to clean....  so tired 
['Yay ', 'time ', 'to ', ' so ', 'tired ']
@user brilliant news for potential young buyers!  
['user ', 'brilliant ', 'news ', 'for ', 'potential ', 'young ']
Seriously tho if you need me anytime over winter break just shoot me a text. Probably won't respond cuz I'll most likely be eating, but hey 
['Seriously ', 'tho ', 'if ', 'you ', 'need ', 'me ', 'anytime ', 'over ', 'winter ', 'break ', 'just ', 'shoot ', 'me ', 'a ', ' Probably ', "won't ", 'respond ', 'cuz ', "I'll ", 'most ', 'likely ', 'be ', ' but ', 'hey ']
@user @user Me and Cam Newton will be engaged by the end of this year just wait on it lmao" BYYER FOOLISHA"<<good night 
['user ', 'user ', 'Me ', 'and ', 'Cam ', 'Newton ', 'will ', '

In [ ]:
r"\w+-\w+|\w+'\w+|\w+|[.&?%!#…]+"
WORD_HASHTAG = "#\w+"